# Questions to the data
1. Does the number of hauses in all houses groups remain stable or there were a construction side finished in the given time frame?
2. What was the weather in the region?
3. What was the price for gas/oil/elictricity?

In [74]:
import pandas as pd
import numpy as np
from datetime import datetime
from typing import List, Tuple, Any

import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
import warnings
warnings.filterwarnings("ignore")

In [75]:
data = pd.read_csv('../data/public_data/train.csv')
final_index = data['pseudo_id']

In [76]:
# drop index for feature preparation
data_ = data.drop(columns='pseudo_id')
# convert dates to pandas datetime
data_.columns = [datetime.strptime(c, "%Y-%m-%d %H:%M:%S") for c in data_.columns]
data_.head()

2017-01-01 00:00:00  2017-01-01 00:30:00  2017-01-01 01:00:00  \
0               45.023              39.9850              36.5695   
1                2.931               1.6410               2.2600   
2               11.014              12.6525              10.8240   
3               55.813              49.0400              49.0950   
4               26.925              28.1180              25.6000   

   2017-01-01 01:30:00  2017-01-01 02:00:00  2017-01-01 02:30:00  \
0              34.7480               35.972               38.439   
1               2.2730                2.651                3.137   
2              13.7485               12.383               12.342   
3              41.1330               45.660               48.477   
4              28.0910               26.530               23.858   

   2017-01-01 03:00:00  2017-01-01 03:30:00  2017-01-01 04:00:00  \
0               36.591              36.3155              32.6605   
1                2.532               3.1420               2.5280   
2               13.413              11.4840              11.5105   
3               50.539              45.7370              42.6800   
4               26.556              27.7140              23.1740   

   2017-01-01 04:30:00  ...  2019-08-28 19:00:00  2019-08-28 19:30:00  \
0               0.1420  ...              24.2880               23.994   
1               0.0000  ...               2.5700                1.446   
2               0.0455  ...               6.3565                5.766   
3               0.0000  ...              32.6460               30.439   
4               0.0000  ...              13.3980               13.280   

   2019-08-28 20:00:00  2019-08-28 20:30:00  2019-08-28 21:00:00  \
0              26.1995              25.0270              23.0665   
1               1.5230               1.5630               2.5880   
2               5.4955               5.0885               6.8140   
3              30.2470              31.2660              34.3390   
4              13.7340              13.6060              14.7000   

   2019-08-28 21:30:00  2019-08-28 22:00:00  2019-08-28 22:30:00  \
0               26.093              23.4295              25.4715   
1                2.190               1.4860               2.5270   
2                7.492               5.7705               6.8240   
3               33.076              33.1080              33.7260   
4               16.290              15.1240              15.3650   

   2019-08-28 23:00:00  2019-08-28 23:30:00  
0               26.246              22.6020  
1                2.288               1.7940  
2                6.072               6.7205  
3               30.009              34.8400  
4               14.360              13.9350  

[5 rows x 39504 columns]

In [77]:
freq = "H"
data_ = data_.T.resample(freq).sum()
data_.head()

0      1        2        3       4       5       6   \
2017-01-01 00:00:00  85.0080  4.572  23.6665  104.853  55.043  21.670   8.517   
2017-01-01 01:00:00  71.3175  4.533  24.5725   90.228  53.691  20.802   9.665   
2017-01-01 02:00:00  74.4110  5.788  24.7250   94.137  50.388  20.309  10.970   
2017-01-01 03:00:00  72.9065  5.674  24.8970   96.276  54.270  19.099   9.228   
2017-01-01 04:00:00  32.8025  2.528  11.5560   42.680  23.174   8.557   3.721   

                          7        8       9   ...     51      52     53  \
2017-01-01 00:00:00  50.1745  74.8950  22.242  ...  0.368  11.430  9.319   
2017-01-01 01:00:00  47.1655  63.5045  21.320  ...  0.680  11.414  9.950   
2017-01-01 02:00:00  51.7245  62.5770  23.942  ...  1.400  14.907  8.828   
2017-01-01 03:00:00  49.3040  64.9425  21.885  ...  0.803  12.920  8.203   
2017-01-01 04:00:00  23.9510  26.9285  10.102  ...  0.205   6.317  3.524   

                        54     55     56     57      58      59     60  
2017-01-01 00:00:00  1.745  5.848  1.232  3.041  6.9575  2.0065  6.693  
2017-01-01 01:00:00  1.807  8.823  0.669  2.868  5.6150  1.4100  5.698  
2017-01-01 02:00:00  1.650  8.535  0.645  2.892  6.6505  1.5015  5.953  
2017-01-01 03:00:00  1.362  5.721  1.418  3.190  7.4195  1.2500  6.856  
2017-01-01 04:00:00  0.869  2.667  0.303  1.803  3.7660  0.7975  1.632  

[5 rows x 61 columns]

In [78]:
# features["hour"] = data.index.hour
data_.columns = [c+1 for c in range(len(data_.columns))]
data_.head()

1      2        3        4       5       6       7   \
2017-01-01 00:00:00  85.0080  4.572  23.6665  104.853  55.043  21.670   8.517   
2017-01-01 01:00:00  71.3175  4.533  24.5725   90.228  53.691  20.802   9.665   
2017-01-01 02:00:00  74.4110  5.788  24.7250   94.137  50.388  20.309  10.970   
2017-01-01 03:00:00  72.9065  5.674  24.8970   96.276  54.270  19.099   9.228   
2017-01-01 04:00:00  32.8025  2.528  11.5560   42.680  23.174   8.557   3.721   

                          8        9       10  ...     52      53     54  \
2017-01-01 00:00:00  50.1745  74.8950  22.242  ...  0.368  11.430  9.319   
2017-01-01 01:00:00  47.1655  63.5045  21.320  ...  0.680  11.414  9.950   
2017-01-01 02:00:00  51.7245  62.5770  23.942  ...  1.400  14.907  8.828   
2017-01-01 03:00:00  49.3040  64.9425  21.885  ...  0.803  12.920  8.203   
2017-01-01 04:00:00  23.9510  26.9285  10.102  ...  0.205   6.317  3.524   

                        55     56     57     58      59      60     61  
2017-01-01 00:00:00  1.745  5.848  1.232  3.041  6.9575  2.0065  6.693  
2017-01-01 01:00:00  1.807  8.823  0.669  2.868  5.6150  1.4100  5.698  
2017-01-01 02:00:00  1.650  8.535  0.645  2.892  6.6505  1.5015  5.953  
2017-01-01 03:00:00  1.362  5.721  1.418  3.190  7.4195  1.2500  6.856  
2017-01-01 04:00:00  0.869  2.667  0.303  1.803  3.7660  0.7975  1.632  

[5 rows x 61 columns]

In [79]:
# check wether datetime in ascending order , it is important for time series
print(data_.index.is_monotonic)

True


In [80]:
data_[(data_.index >='2017-02-08 00:00:00') & (data_.index <= '2017-02-14 23:00:00')]

1    2    3    4    5    6    7    8    9    10  ...  \
2017-02-08 00:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-08 01:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-08 02:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-08 03:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-08 04:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
...                  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
2017-02-14 19:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-14 20:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-14 21:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-14 22:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2017-02-14 23:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   

                      52   53   54   55   56   57   58   59   60   61  
2017-02-08 00:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-08 01:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-08 02:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-08 03:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-08 04:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...                  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
2017-02-14 19:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-14 20:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-14 21:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-14 22:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2017-02-14 23:00:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[168 rows x 61 columns]

In [81]:
# Set dates for development phase
new_date_range = pd.date_range(start="2017-01-01", end="2019-03-31", freq="H")

data_ = data_.reindex(new_date_range)

In [82]:
# saving indexes for next steps
idx_test_date = data_.index[data_[1] == 0]
idx_test_date

DatetimeIndex(['2017-02-08 00:00:00', '2017-02-08 01:00:00',
               '2017-02-08 02:00:00', '2017-02-08 03:00:00',
               '2017-02-08 04:00:00', '2017-02-08 05:00:00',
               '2017-02-08 06:00:00', '2017-02-08 07:00:00',
               '2017-02-08 08:00:00', '2017-02-08 09:00:00',
               ...
               '2019-03-21 14:00:00', '2019-03-21 15:00:00',
               '2019-03-21 16:00:00', '2019-03-21 17:00:00',
               '2019-03-21 18:00:00', '2019-03-21 19:00:00',
               '2019-03-21 20:00:00', '2019-03-21 21:00:00',
               '2019-03-21 22:00:00', '2019-03-21 23:00:00'],
              dtype='datetime64[ns]', length=3024, freq=None)

In [83]:
idx_test_date[0:168]

DatetimeIndex(['2017-02-08 00:00:00', '2017-02-08 01:00:00',
               '2017-02-08 02:00:00', '2017-02-08 03:00:00',
               '2017-02-08 04:00:00', '2017-02-08 05:00:00',
               '2017-02-08 06:00:00', '2017-02-08 07:00:00',
               '2017-02-08 08:00:00', '2017-02-08 09:00:00',
               ...
               '2017-02-14 14:00:00', '2017-02-14 15:00:00',
               '2017-02-14 16:00:00', '2017-02-14 17:00:00',
               '2017-02-14 18:00:00', '2017-02-14 19:00:00',
               '2017-02-14 20:00:00', '2017-02-14 21:00:00',
               '2017-02-14 22:00:00', '2017-02-14 23:00:00'],
              dtype='datetime64[ns]', length=168, freq=None)

In [84]:
data_ = data_.fillna(method="backfill")

In [85]:
#plt.rcParams.update({'figure.figsize':(9,3), 'figure.dpi':160})
#data_[1].plot()
#plt.title('Energy use forecasts for houshold group' + " 1")
#plt.show()

In [86]:
data_\
    .isna()\
    .sum()\
    .to_frame()\
    .assign(perc = lambda row: 100 * row[0] / data_.shape[0])\
    .rename(columns={0: 'Number of missed data  points', 'perc': '% of missed data points'})

Number of missed data  points  % of missed data points
1                               0                      0.0
2                               0                      0.0
3                               0                      0.0
4                               0                      0.0
5                               0                      0.0
..                            ...                      ...
57                              0                      0.0
58                              0                      0.0
59                              0                      0.0
60                              0                      0.0
61                              0                      0.0

[61 rows x 2 columns]

# Adding features

In [87]:
def day_part(hour):
    part_of_day = 0
    if 0 <= hour <= 6:
        part_of_day = 1
    elif 6 < hour <= 12:
        part_of_day = 2
    elif 12 < hour <= 18:
        part_of_day = 3
    elif 18 < hour <= 23:
        part_of_day = 4
    return part_of_day

In [88]:
df = data_.copy(deep=True)
#df.drop(columns=['ord_mean_week','mean','std'],inplace=True)
df["weekday"] = data_.index.weekday
df["dayofyear"] = data_.index.dayofyear
df["is_weekend"] = data_.index.weekday.isin([5, 6]).astype(np.int32)
df["month"] = data_.index.month
df["season"] = (data_.index.month % 12 + 3) // 3
df['Hour'] = df.index.hour
df['type_of_the_day'] = df.apply(lambda row : day_part(row['Hour']), axis = 1)

In [89]:
def create_features(houshold_id,df=df) -> pd.DataFrame:
    df_new = df[[houshold_id, "weekday", "dayofyear", "is_weekend", "season", "month","type_of_the_day"]]
    df_new['std'] = df_new[houshold_id].rolling(12).std().fillna(method="backfill")
    df_new['mean'] = df_new[houshold_id].rolling(12).mean().fillna(method="backfill")
    df_new['std'] = df_new[houshold_id].rolling(24).std().fillna(method="backfill")
    df_new['mean'] = df_new[houshold_id].rolling(24).mean().fillna(method="backfill")
    df_new['lag_1'] = df[houshold_id].shift(1).fillna(method="backfill")
    df_new['lag_2'] = df[houshold_id].shift(2).fillna(method="backfill")
    df_new['lag_3'] = df_new[houshold_id].shift(3).fillna(method="backfill")
    df_new['lag_4'] = df_new[houshold_id].shift(4).fillna(method="backfill")
    df_new['lag_5'] = df_new[houshold_id].shift(5).fillna(method="backfill")
    df_new['lag_6'] = df_new[houshold_id].shift(6).fillna(method="backfill")
    df_new['lag_7'] = df_new[houshold_id].shift(7).fillna(method="backfill")
    df_new['lag_8'] = df_new[houshold_id].shift(8).fillna(method="backfill")
    df_new['lag_9'] = df_new[houshold_id].shift(9).fillna(method="backfill")
    df_new['lag_10'] = df_new[houshold_id].shift(10).fillna(method="backfill")
    df_new['lag_11'] = df_new[houshold_id].shift(11).fillna(method="backfill")
    df_new['lag_12'] = df_new[houshold_id].shift(12).fillna(method="backfill")
    df_new['lag_13'] = df_new[houshold_id].shift(13).fillna(method="backfill")
    df_new['lag_14'] = df_new[houshold_id].shift(14).fillna(method="backfill")
    df_new['lag_15'] = df_new[houshold_id].shift(15).fillna(method="backfill")
    df_new['lag_16'] = df_new[houshold_id].shift(16).fillna(method="backfill")
    df_new['lag_17'] = df_new[houshold_id].shift(17).fillna(method="backfill")
    df_new['lag_18'] = df_new[houshold_id].shift(18).fillna(method="backfill")
    return df_new

In [90]:
def get_weeks(idx)-> List[List[pd._libs.tslibs.timestamps.Timestamp]]:
    idx = list(idx)
    count = 0
    hours_to_predict = []
    hours = []
    for i in range(len(idx)):
        if count > 167:
            hours_to_predict.append(hours)
            hours = []
            count = 0
        hours.append(idx[i])
        count += 1
    return hours_to_predict

In [91]:
hours_test_date = get_weeks(idx_test_date)

In [92]:
len(hours_test_date[0])

168

In [93]:
def data_split_accumlated(result, weeks, n, houshold) -> Tuple[Any, Any]:
    print(weeks[n])
    result_splitted = result[result.index < weeks[n][0]]
    result_splitted_features = result_splitted.drop([houshold], axis=1)
    result_splitted_target = result_splitted[houshold]
    #print("target: ", result_splitted_target)
    result_splitted_to_predict = result[(result.index >= weeks[n][0]) & (result.index <= weeks[n][167])]
    result_splitted_to_predict_features = result_splitted_to_predict.drop([houshold], axis=1)
    result_splitted_to_predict_target = result_splitted_to_predict[houshold]
    result_splitted_to_predict_target = result_splitted_to_predict_target.to_frame()

    return result_splitted_features, result_splitted_target, result_splitted_to_predict_features, result_splitted_to_predict_target

In [94]:
all_predictions = []
 
for houshold in data_.columns:
    houshold_predictions = []
    print("***** Houshold " + str(houshold) + " dataset created ****** ")
    for week in range(len(hours_test_date)):
        #print("week "+  str(week) + " splitting started")
        result = create_features(houshold)
        features, target, features_predict, target_predict = data_split_accumlated(result, hours_test_date, week, houshold)
        model_linear = LinearRegression()
        model_linear.fit(features, target)
        print("trained on " + str(week))
        prediction = model_linear.predict(features_predict)
        houshold_predictions.append(prediction)
        week_timestamps = hours_test_date[week]
        target_predict['predict'] = prediction
        df.loc[week_timestamps[0]:week_timestamps[6],houshold] = target_predict['predict']
        print("=============================================")
        print(prediction)
        #print(df.loc[week_timestamps[0]:week_timestamps[6],houshold])
        print("=============================================")
    all_predictions.append(houshold_predictions)

***** Houshold 1 dataset created ****** 
[Timestamp('2017-02-08 00:00:00'), Timestamp('2017-02-08 01:00:00'), Timestamp('2017-02-08 02:00:00'), Timestamp('2017-02-08 03:00:00'), Timestamp('2017-02-08 04:00:00'), Timestamp('2017-02-08 05:00:00'), Timestamp('2017-02-08 06:00:00'), Timestamp('2017-02-08 07:00:00'), Timestamp('2017-02-08 08:00:00'), Timestamp('2017-02-08 09:00:00'), Timestamp('2017-02-08 10:00:00'), Timestamp('2017-02-08 11:00:00'), Timestamp('2017-02-08 12:00:00'), Timestamp('2017-02-08 13:00:00'), Timestamp('2017-02-08 14:00:00'), Timestamp('2017-02-08 15:00:00'), Timestamp('2017-02-08 16:00:00'), Timestamp('2017-02-08 17:00:00'), Timestamp('2017-02-08 18:00:00'), Timestamp('2017-02-08 19:00:00'), Timestamp('2017-02-08 20:00:00'), Timestamp('2017-02-08 21:00:00'), Timestamp('2017-02-08 22:00:00'), Timestamp('2017-02-08 23:00:00'), Timestamp('2017-02-09 00:00:00'), Timestamp('2017-02-09 01:00:00'), Timestamp('2017-02-09 02:00:00'), Timestamp('2017-02-09 03:00:00'), Timest

In [95]:
weeks_columns = [week for weeks in hours_test_date for week in weeks]
weeks_columns

[Timestamp('2017-02-08 00:00:00'),
 Timestamp('2017-02-08 01:00:00'),
 Timestamp('2017-02-08 02:00:00'),
 Timestamp('2017-02-08 03:00:00'),
 Timestamp('2017-02-08 04:00:00'),
 Timestamp('2017-02-08 05:00:00'),
 Timestamp('2017-02-08 06:00:00'),
 Timestamp('2017-02-08 07:00:00'),
 Timestamp('2017-02-08 08:00:00'),
 Timestamp('2017-02-08 09:00:00'),
 Timestamp('2017-02-08 10:00:00'),
 Timestamp('2017-02-08 11:00:00'),
 Timestamp('2017-02-08 12:00:00'),
 Timestamp('2017-02-08 13:00:00'),
 Timestamp('2017-02-08 14:00:00'),
 Timestamp('2017-02-08 15:00:00'),
 Timestamp('2017-02-08 16:00:00'),
 Timestamp('2017-02-08 17:00:00'),
 Timestamp('2017-02-08 18:00:00'),
 Timestamp('2017-02-08 19:00:00'),
 Timestamp('2017-02-08 20:00:00'),
 Timestamp('2017-02-08 21:00:00'),
 Timestamp('2017-02-08 22:00:00'),
 Timestamp('2017-02-08 23:00:00'),
 Timestamp('2017-02-09 00:00:00'),
 Timestamp('2017-02-09 01:00:00'),
 Timestamp('2017-02-09 02:00:00'),
 Timestamp('2017-02-09 03:00:00'),
 Timestamp('2017-02-

In [96]:
def flatten(hous):
    return [week for weeks in hous for week in weeks]

In [97]:
flatened_predictions = []
for hous in all_predictions:
    flatened_predictions.append(flatten(hous))

In [98]:
df_from_list = pd.DataFrame([i for i in flatened_predictions], columns= [weeks_columns],index = final_index)

In [99]:
df_from_list.reset_index(inplace = True)

In [100]:
df_from_list.to_csv("./sample_submission_hourly_max.csv", index = False)

In [101]:
df_from_list

pseudo_id 2017-02-08 00:00:00  \
0   0x16cb02173ebf3059efdc97fd1819f14a2           52.970871   
1   0x1c9d08cd16fce04790ef900695861e786            3.671509   
2   0x1612e4cbe3b1b85c3dbcaeaa504ee8424           15.254707   
3   0x20158d36236a640cf0524dba149459169          145.096335   
4    0xc305005dcb1ed6128d816954c5ab9e7e           24.698450   
..                                  ...                 ...   
56  0x12342fbadc0ca9418f2d540bb3cb8364a            0.845093   
57  0x16d1816bc5d185c47de080d4c6a64bc9a            1.884297   
58  0x14f480f24c435af1b8574c1c6bab38a1c            4.412996   
59  0x1c7fc724d0a4f89ed1de8a0a4b302db22            2.087085   
60  0x187454451b5ef5c6ad7377c21d9adbfe2            3.192436   

   2017-02-08 01:00:00 2017-02-08 02:00:00 2017-02-08 03:00:00  \
0            38.447541           33.497795           32.630874   
1             2.911621            3.013306            2.634644   
2             9.414444            8.456389            8.626634   
3            90.673357           72.388824           82.273364   
4            17.653130           14.159553           12.705279   
..                 ...                 ...                 ...   
56            0.767822            0.652344            0.619141   
57            1.345981            1.200327            1.047610   
58            3.000830            3.007403            2.638632   
59            1.387107            1.073060            0.838250   
60            2.377824            1.724005            1.669606   

   2017-02-08 04:00:00 2017-02-08 05:00:00 2017-02-08 06:00:00  \
0            24.707513           22.621193           20.974909   
1             1.890259            2.009766            2.244873   
2             6.431578            7.209828            7.865981   
3            58.285265           52.832710           53.290473   
4             9.202791            8.924982           10.493703   
..                 ...                 ...                 ...   
56            0.459839            0.470581            0.404541   
57            0.816995            0.923950            0.924587   
58            1.888477            1.764045            1.854852   
59            0.326646            0.318226            0.381584   
60            1.905275            1.295123            1.447891   

   2017-02-08 07:00:00 2017-02-08 08:00:00  ... 2019-02-04 14:00:00  \
0            17.846901           14.402119  ...           -0.268525   
1             1.392700            1.617432  ...           -0.021239   
2             7.569841            7.628716  ...            0.024037   
3            48.573540           35.940441  ...           -0.209693   
4             6.997908            5.658858  ...           -0.033067   
..                 ...                 ...  ...                 ...   
56            0.326904            0.393311  ...           -0.015880   
57            0.753490            0.746900  ...           -0.010621   
58            1.265271            1.259429  ...           -0.087697   
59            0.371294            0.323338  ...            0.005732   
60            1.603902            1.302542  ...           -0.033831   

   2019-02-04 15:00:00 2019-02-04 16:00:00 2019-02-04 17:00:00  \
0            -0.268525           -0.268525           -0.268525   
1            -0.021239           -0.021239           -0.021239   
2             0.024037            0.024037            0.024037   
3            -0.209693           -0.209693           -0.209693   
4            -0.033067           -0.033067           -0.033067   
..                 ...                 ...                 ...   
56           -0.015880           -0.015880           -0.015880   
57           -0.010621           -0.010621           -0.010621   
58           -0.087697           -0.087697           -0.087697   
59            0.005732            0.005732            0.005732   
60           -0.033831           -0.033831           -0.033831   

   2019-02-04 18:00:00 2019-02-04 19:00:0

In [102]:
import eli5
from eli5.sklearn import PermutationImportance

In [103]:
feature_names = list(features.columns)

In [104]:
features

weekday  dayofyear  is_weekend  season  month  \
2017-01-01 00:00:00        6          1           1       1      1   
2017-01-01 01:00:00        6          1           1       1      1   
2017-01-01 02:00:00        6          1           1       1      1   
2017-01-01 03:00:00        6          1           1       1      1   
2017-01-01 04:00:00        6          1           1       1      1   
...                      ...        ...         ...     ...    ...   
2019-01-28 19:00:00        0         28           0       1      1   
2019-01-28 20:00:00        0         28           0       1      1   
2019-01-28 21:00:00        0         28           0       1      1   
2019-01-28 22:00:00        0         28           0       1      1   
2019-01-28 23:00:00        0         28           0       1      1   

                     type_of_the_day       std      mean  lag_1  lag_2  ...  \
2017-01-01 00:00:00                1  1.091843  4.671333  6.693  6.693  ...   
2017-01-01 01:00:00                1  1.091843  4.671333  6.693  6.693  ...   
2017-01-01 02:00:00                1  1.091843  4.671333  5.698  6.693  ...   
2017-01-01 03:00:00                1  1.091843  4.671333  5.953  5.698  ...   
2017-01-01 04:00:00                1  1.091843  4.671333  6.856  5.953  ...   
...                              ...       ...       ...    ...    ...  ...   
2019-01-28 19:00:00                4  1.373356  5.739083  8.475  6.423  ...   
2019-01-28 20:00:00                4  1.481148  5.595042  5.852  8.475  ...   
2019-01-28 21:00:00                4  1.453722  5.646917  2.915  5.852  ...   
2019-01-28 22:00:00                4  1.469672  5.613583  5.500  2.915  ...   
2019-01-28 23:00:00                4  1.485658  5.556417  4.560  5.500  ...   

                     lag_9  lag_10  lag_11  lag_12  lag_13  lag_14  lag_15  \
2017-01-01 00:00:00  6.693   6.693   6.693   6.693   6.693   6.693   6.693   
2017-01-01 01:00:00  6.693   6.693   6.693   6.693   6.693   6.693   6.693   
2017-01-01 02:00:00  6.693   6.693   6.693   6.693   6.693   6.693   6.693   
2017-01-01 03:00:00  6.693   6.693   6.693   6.693   6.693   6.693   6.693   
2017-01-01 04:00:00  6.693   6.693   6.693   6.693   6.693   6.693   6.693   
...                    ...     ...     ...     ...     ...     ...     ...   
2019-01-28 19:00:00  5.950   4.236   4.924   6.611   6.035   3.494   6.072   
2019-01-28 20:00:00  8.827   5.950   4.236   4.924   6.611   6.035   3.494   
2019-01-28 21:00:00  4.467   8.827   5.950   4.236   4.924   6.611   6.035   
2019-01-28 22:00:00  5.051   4.467   8.827   5.950   4.236   4.924   6.611   
2019-01-28 23:00:00  6.581   5.051   4.467   8.827   5.950   4.236   4.924   

                     lag_16  lag_17  lag_18  
2017-01-01 00:00:00   6.693   6.693   6.693  
2017-01-01 01:00:00   6.693   6.693   6.693  
2017-01-01 02:00:00   6.693   6.693   6.693  
2017-01-01 03:00:00   6.693   6.693   6.693  
2017-01-01 04:00:00   6.693   6.693   6.693  
...                     ...     ...     ...  
2019-01-28 19:00:00   4.776   5.064   3.867  
2019-01-28 20:00:00   6.072   4.776   5.064  
2019-01-28 21:00:00   3.494   6.072   4.776  
2019-01-28 22:00:00   6.035   3.494   6.072  
2019-01-28 23:00:00   6.611   6.035   3.494  

[18192 rows x 26 columns]

In [105]:
eli5.explain_weights(model_linear, top=40, feature_names = feature_names)

Explanation(estimator='LinearRegression()', description="\nFeatures with largest coefficients.\nCaveats:\n1. Be careful with features which are not\n   independent - weights don't show their importance.\n2. If scale of input features is different then scale of coefficients\n   will also be different, making direct comparison between coefficient values\n   incorrect.\n3. Depending on regularization, rare features sometimes may have high\n   coefficients; this doesn't mean they contribute much to the\n   classification result for most examples.\n", error=None, method='linear model', is_regression=True, targets=[TargetExplanation(target='y', feature_weights=FeatureWeights(pos=[FeatureWeight(feature='mean', weight=1.8305692931322073, std=None, value=None), FeatureWeight(feature='std', weight=0.26735958162575973, std=None, value=None), FeatureWeight(feature='lag_1', weight=0.179795164100654, std=None, value=None), FeatureWeight(feature='lag_2', weight=0.03428929763005214, std=None, value=None), FeatureWeight(feature='<BIAS>', weight=0.029795494347190754, std=None, value=None), FeatureWeight(feature='lag_7', weight=0.019394297075717812, std=None, value=None), FeatureWeight(feature='weekday', weight=0.013346257255555062, std=None, value=None), FeatureWeight(feature='lag_4', weight=0.010355095167419403, std=None, value=None), FeatureWeight(feature='lag_3', weight=0.009820906569068649, std=None, value=None), FeatureWeight(feature='dayofyear', weight=0.0007838192673950209, std=None, value=None), FeatureWeight(feature='season', weight=0.0004449281914413265, std=None, value=None)], neg=[FeatureWeight(feature='lag_12', weight=-0.16568350734096846, std=None, value=None), FeatureWeight(feature='lag_18', weight=-0.16430592478305525, std=None, value=None), FeatureWeight(feature='lag_15', weight=-0.1277160377679724, std=None, value=None), FeatureWeight(feature='lag_17', weight=-0.12515060438299236, std=None, value=None), FeatureWeight(feature='lag_16', weight=-0.11964379977889705, std=None, value=None), FeatureWeight(feature='lag_9', weight=-0.11067748725662915, std=None, value=None), FeatureWeight(feature='lag_13', weight=-0.09308267325389559, std=None, value=None), FeatureWeight(feature='lag_8', weight=-0.05651548136458319, std=None, value=None), FeatureWeight(feature='lag_10', weight=-0.05361238047890976, std=None, value=None), FeatureWeight(feature='is_weekend', weight=-0.05321479310433849, std=None, value=None), FeatureWeight(feature='lag_6', weight=-0.05299280333332665, std=None, value=None), FeatureWeight(feature='lag_11', weight=-0.03530227292861721, std=None, value=None), FeatureWeight(feature='lag_14', weight=-0.030912112125353552, std=None, value=None), FeatureWeight(feature='lag_5', weight=-0.027440110448139373, std=None, value=None), FeatureWeight(feature='month', weight=-0.02555321406747482, std=None, value=None), FeatureWeight(feature='type_of_the_day', weight=-0.013466068059710026, std=None, value=None)], pos_remaining=0, neg_remaining=0), proba=None, score=None, weighted_spans=None, heatmap=None)], feature_importances=None, decision_tree=None, highlight_spaces=None, transition_features=None, image=None)

In [106]:
perm = PermutationImportance(model_linear).fit(features, target)
eli5.show_weights(perm,top=50,feature_names = feature_names)